In [2]:
%tensorflow_version 1.x
import tensorflow as tf

# Download the code
!git clone https://github.com/NVlabs/stylegan2.git
%cd stylegan2
!nvcc test_nvcc.cu -o test_nvcc -run

Cloning into 'stylegan2'...
remote: Enumerating objects: 93, done.
remote: Total 93 (delta 0), reused 0 (delta 0), pack-reused 93
Unpacking objects: 100% (93/93), done.
/content/stylegan2/stylegan2
CPU says hello.
GPU says hello.


In [4]:
# Download the model of choice
import argparse
import numpy as np
import PIL.Image
import dnnlib
import dnnlib.tflib as tflib
import re
import sys
from io import BytesIO
import IPython.display
import numpy as np
from math import ceil
from PIL import Image, ImageDraw
import imageio
import random
import os

import pretrained_networks

network_pkl = "gdrive:networks/stylegan2-ffhq-config-f.pkl"

# If downloads fails, due to 'Google Drive download quota exceeded' you can try downloading manually from your own Google Drive account
# network_pkl = "/content/drive/My Drive/GAN/stylegan2-ffhq-config-f.pkl"

print('Loading networks from "%s"...' % network_pkl)
_G, _D, Gs = pretrained_networks.load_networks(network_pkl)
noise_vars = [var for name, var in Gs.components.synthesis.vars.items() if name.startswith('noise')]

#Set up file structure for later use
!mkdir vectors

Loading networks from "gdrive:networks/stylegan2-ffhq-config-f.pkl"...
mkdir: cannot create directory ‘vectors’: File exists


In [0]:
def generate_zs_from_seeds(seeds):
    zs = []
    for seed_idx, seed in enumerate(seeds):
        rnd = np.random.RandomState(seed)
        z = rnd.randn(1, *Gs.input_shape[1:]) # [minibatch, component]
        zs.append(z)
    return zs

def generate_images(zs, truncation_psi):
    Gs_kwargs = dnnlib.EasyDict()
    Gs_kwargs.output_transform = dict(func=tflib.convert_images_to_uint8, nchw_to_nhwc=True)
    Gs_kwargs.randomize_noise = False
    if not isinstance(truncation_psi, list):
        truncation_psi = [truncation_psi] * len(zs)
        
    imgs = []
    for z_idx, z in log_progress(enumerate(zs), size = len(zs), name = "Generating images"):
        Gs_kwargs.truncation_psi = truncation_psi[z_idx]
        noise_rnd = np.random.RandomState(1) # fix noise
        tflib.set_vars({var: noise_rnd.randn(*var.shape.as_list()) for var in noise_vars}) # [height, width]
        images = Gs.run(z, None, **Gs_kwargs) # [minibatch, height, width, channel]
        imgs.append(PIL.Image.fromarray(images[0], 'RGB'))
    return imgs

# Taken from https://github.com/alexanderkuk/log-progress
def log_progress(sequence, every=1, size=None, name='Items'):
    from ipywidgets import IntProgress, HTML, VBox
    from IPython.display import display

    is_iterator = False
    if size is None:
        try:
            size = len(sequence)
        except TypeError:
            is_iterator = True
    if size is not None:
        if every is None:
            if size <= 200:
                every = 1
            else:
                every = int(size / 200)     # every 0.5%
    else:
        assert every is not None, 'sequence is iterator, set every'

    if is_iterator:
        progress = IntProgress(min=0, max=1, value=1)
        progress.bar_style = 'info'
    else:
        progress = IntProgress(min=0, max=size, value=0)
    label = HTML()
    box = VBox(children=[label, progress])
    display(box)

    index = 0
    try:
        for index, record in enumerate(sequence, 1):
            if index == 1 or index % every == 0:
                if is_iterator:
                    label.value = '{name}: {index} / ?'.format(
                        name=name,
                        index=index
                    )
                else:
                    progress.value = index
                    label.value = u'{name}: {index} / {size}'.format(
                        name=name,
                        index=index,
                        size=size
                    )
            yield record
    except:
        progress.bar_style = 'danger'
        raise
    else:
        progress.bar_style = 'success'
        progress.value = index
        label.value = "{name}: {index}".format(
            name=name,
            index=str(index or '?')
        )


def imshow(a, format='png', jpeg_fallback=True):
  a = np.asarray(a, dtype=np.uint8)
  str_file = BytesIO()
  PIL.Image.fromarray(a).save(str_file, format)
  im_data = str_file.getvalue()
  try:
    disp = IPython.display.display(IPython.display.Image(im_data))
  except IOError:
    if jpeg_fallback and format != 'jpeg':
      print ('Warning: image was too large to display in format "{}"; '
             'trying jpeg instead.').format(format)
      return imshow(a, format='jpeg')
    else:
      raise
  return disp

def load_latents(folder_path, prefix):
  loaded_latents = []
  for file_name in os.listdir(folder_path):
    if file_name.startswith(prefix):
      loaded_latent = np.loadtxt(os.path.join(folder_path, file_name), delimiter=',')
      loaded_latent = loaded_latent.reshape((1,512))
      loaded_latents.append(loaded_latent)

  return loaded_latents

def make_cusred(latent_vector):
  for i in range(364,1000):
    cursed_image = generate_images([latent_vector], 0.7 + 3.0*(float(i)/1000.0))[0]
    cursed_image.save('/content/stylegan2/vectors/{}.png'.format(i))

def sign (p1, p2, p3):
    
    return (p1[0] - p3[0]) * (p2[1] - p3[1]) - (p2[0] - p3[0]) * (p1[1] - p3[1])

def point_in_triangle (pt, v1, v2, v3):
    
    d1 = sign(pt, v1, v2)
    d2 = sign(pt, v2, v3)
    d3 = sign(pt, v3, v1)

    has_neg = (d1 < 0) or (d2 < 0) or (d3 < 0)
    has_pos = (d1 > 0) or (d2 > 0) or (d3 > 0)

    return not(has_neg and has_pos)

def random_point_in_triangle(p1, p2, p3):
    v1 = p2 - p1
    v2 = p3 - p1
    v1_mag = np.linalg.norm(v1)
    v2_mag = np.linalg.norm(v2)
    theta = np.arccos(np.dot(v1, v2)/(v1_mag*v2_mag))
    
    origin = np.array([0,0])
    side1 = np.array([v1_mag,0])
    side2 = np.array([v2_mag * np.cos(theta), v2_mag * np.sin(theta)])
    
    while(True):
        random_point = np.array([random.random() * v1_mag, random.random() * v2_mag * np.sin(theta)])
        if point_in_triangle (random_point, origin, side1, side2):
            #x.append(random_point[0])
            #y.append(random_point[1])
            #Subtract the projection of v2 onto v1 from v2 to get a perpendicular vector from v1 to p3
            #Use th
            perp_vector = v2 - (np.dot(v2,v1)/v1_mag**2)*v1

            transformed_random_point = p1 + random_point[0]/v1_mag * v1 + random_point[1]/v2_mag * perp_vector
            yield transformed_random_point  

In [0]:
#Saving and loading a latent vector
#np.savetxt('/content/stylegan2/vectors/b4.vec', latent_vector[0], delimiter=',')



In [0]:
history = []
# \simple_face_finder_work_folder\random_face_and_vecs

In [0]:
latent_vector = generate_zs_from_seeds([random.randint(0,1000000)])
history.append(latent_vector)
imshow(generate_images(latent_vector, 0.7)[0])

In [9]:
from google.colab import drive
drive.mount('/content/drive', force_remount=True)


Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/drive


In [0]:
!cp  -a "/content/stylegan2/vectors/." "/content/drive/My Drive/Cursed_Images(1)/"

In [0]:
latents = load_latents( '/content/drive/My Drive/glasses_net_data/no_glasses/', "ns")

In [0]:
#latents
len(latents)

# for i in range(500):
#   nodes = random.sample(range(20), 2)
#   diff = latents[nodes[1]] - latents[nodes[0]]
#   tween = latents[nodes[0]] + diff * np.random.uniform(.3,.7)
#   generate_images([tween], 0.7)[0].save('/content/drive/My Drive/linear_samples/lin{}.png'.format(i))


172

In [0]:
for i in range(0,1000):
  nodes = random.sample(range(len(latents)),3)
  latent_vector = next(random_point_in_triangle(latents[nodes[0]][0], latents[nodes[1]][0], latents[nodes[2]][0]))
  latent_vector = latent_vector.reshape(1,512)
  generate_images([latent_vector], 0.7)[0].save('/content/drive/My Drive/glasses_work_folder/no_glasses_validation/no_spec_val{}.png'.format(i))
  # np.savetxt('/content/drive/My Drive/no_glasses/ns{}.vec'.format(i), latent_vector[0], delimiter=',')


In [10]:
# \simple_face_finder_work_folder\random_face_and_vecs
for i in range(2000):
  latent_vector = generate_zs_from_seeds([random.randint(0,1000000)])[0]
  generate_images([latent_vector], 0.7)[0].save('/content/drive/My Drive/simple_face_finder_work_folder/validation/random_images/random{}.png'.format(i))
  np.savetxt('/content/drive/My Drive/simple_face_finder_work_folder/validation/random_vecs/random{}.vec'.format(i), latent_vector[0], delimiter=',')

# # \simple_face_finder_work_folder\random_face_and_vecs
# latent_vectors = generate_zs_from_seeds([random.randint(0,1000000)] for _ in range(5000))
# images = generate_images(latent_vectors, 0.7)

# for idx, image in images:
#   image.save('/content/drive/My Drive/simple_face_finder_work_folder/random_face_and_vecs/random{}.png'.format(idx))
#   np.savetxt('/content/drive/My Drive/glasses_work_folder/random{}.vec'.format(idx), latent_vectors[idx], delimiter=',')
